In [9]:
import json
import sys
from pathlib import Path
from typing import Any, List
import requests
from tqdm import tqdm
from web3 import Web3
import pandas as pd
import pickle
from concurrent.futures import ThreadPoolExecutor, as_completed

NUM_WORKERS = 10
DEPRECATED_STAKING_PROGRAMS = {
    "quickstart_alpha_everest": "0x5add592ce0a1B5DceCebB5Dcac086Cd9F9e3eA5C",
    "quickstart_alpha_alpine": "0x2Ef503950Be67a98746F484DA0bBAdA339DF3326",
    "quickstart_alpha_coastal": "0x43fB32f25dce34EB76c78C7A42C8F40F84BCD237",
}
STAKING_PROGRAMS_QS = {
    "quickstart_beta_hobbyist": "0x389B46c259631Acd6a69Bde8B6cEe218230bAE8C",
    "quickstart_beta_hobbyist_2": "0x238EB6993b90a978ec6AAD7530d6429c949C08DA",
    "quickstart_beta_expert": "0x5344B7DD311e5d3DdDd46A4f71481bD7b05AAA3e",
    "quickstart_beta_expert_2": "0xb964e44c126410df341ae04B13aB10A985fE3513",
    "quickstart_beta_expert_3": "0x80faD33Cadb5F53f9D29F02Db97D682E8b101618",
}

STAKING_PROGRAMS_PEARL = {
    "pearl_alpha": "0xEE9F19b5DF06c7E8Bfc7B28745dcf944C504198A",
    "pearl_beta": "0xeF44Fb0842DDeF59D37f85D61A1eF492bbA6135d",
    "pearl_beta_2": "0x1c2F82413666d2a3fD8bC337b0268e62dDF67434",
}
SERVICE_REGISTRY_ADDRESS = "0x9338b5153AE39BB89f50468E608eD9d764B755fD"




def check_owner_staking_contract(owner_address: str) -> str:
    staking = ""
    owner_address = owner_address.lower()
    # check quickstart staking contracts
    qs_list = [x.lower() for x in STAKING_PROGRAMS_QS.values()]
    if owner_address in qs_list:
        return "quickstart"

    # check pearl staking contracts
    pearl_list = [x.lower() for x in STAKING_PROGRAMS_PEARL.values()]
    if owner_address in pearl_list:
        return "pearl"

    # check legacy staking contracts
    deprec_list = [x.lower() for x in DEPRECATED_STAKING_PROGRAMS.values()]
    if owner_address in deprec_list:
        return "quickstart"

    return staking


def get_trader_address_staking(trader_address: str) -> str:
    # check if there is any service id linked with that trader address
    with open("../data/service_map.pkl", "rb") as f:
        service_map = pickle.load(f)
    found_key = -1
    for key, value in service_map.items():
        if value["safe_address"].lower() == trader_address.lower():
            # found a service
            found_key = key
            break

    if found_key == -1:
        print("trader address not found in the service map")
        return ""
    owner = service_map[found_key]["owner_address"]
    return check_owner_staking_contract(owner_address=owner)


def label_trades_by_staking(trades_df: pd.DataFrame) -> pd.DataFrame:
    all_traders = trades_df.trader_address.unique()
    trades_df["staking"] = ""
    for trader in tqdm(all_traders, desc="Labeling traders by staking", unit="trader"):
        tqdm.write(f"checking trader {trader}")
        staking_label = get_trader_address_staking(trader)
        if staking_label != "":
            trades_df.loc[trades_df["trader_address"] == trader, "staking"] = staking_label
        tqdm.write(f"statking label {staking_label}")
    return trades_df

In [10]:
trades_df = pd.read_parquet("../data/all_trades_profitability.parquet")
trades_df = label_trades_by_staking(trades_df=trades_df)
print(
    trades_df[
        [
            "trader_address",
            "creation_timestamp",
            "market_creator",
            "staking",
            "collateral_amount",
        ]
    ]
)
print(trades_df.staking.value_counts())

Labeling traders by staking:  51%|█████     | 104/204 [00:00<00:00, 522.80trader/s]

checking trader 0x022b36c50b85b8ae7addfb8a35d76c59d5814834
statking label 
checking trader 0x034c4ad84f7ac6638bf19300d5bbe7d9b981e736
trader address not found in the service map
statking label 
checking trader 0x09e9d42a029e8b0c2df3871709a762117a681d92
statking label 
checking trader 0x0d049dcaece0ecb6fc81a460da7bcc2a4785d6e5
statking label 
checking trader 0x1c1bb5398ba525c5bca07eeade45958e455de4b3
statking label quickstart
checking trader 0x246f6787c409dd5139b7029cd63b7d6aad08cc61
statking label 
checking trader 0x2dd9f5678484c1f59f97ed334725858b938b4102
trader address not found in the service map
statking label 
checking trader 0x3666da333dadd05083fef9ff6ddee588d26e4307
trader address not found in the service map
statking label 
checking trader 0x3a461ae963acf0fedc72a07d060b8e1f44851b28
statking label 
checking trader 0x49f4e3d8edc85efda9b0a36d96e406a59b13fcc2
statking label quickstart
checking trader 0x4e8b85a2b2ffa1f586441d1410f09b416d450d91
statking label 
checking trader 0x55948

Labeling traders by staking:  77%|███████▋  | 157/204 [00:00<00:00, 393.35trader/s]

checking trader 0x64b9afc7343374b8b89a6a83d56e859349722115
statking label 
checking trader 0xe3483992c90fff85ce99b8047ff5988d6a4a9ad9
statking label quickstart
checking trader 0xca6a7735745ab50ba3831ad92437fbb4a49474e4
statking label 
checking trader 0x36ff6381fd5f30c06428b47ed36ee0f8a018d49e
statking label 
checking trader 0xd75b30e0f3093a3a4c90bb14028a21684047884c
statking label 
checking trader 0x20a55f64186b467fa67df63c2b8d2e0d84ecdaa4
statking label pearl
checking trader 0xed907a98de939f9817faa1c6e644922e3ee0cdec
statking label pearl
checking trader 0x360e606b22df1f808366255ef0bbefa425f570f4
statking label pearl
checking trader 0x4b9e1890640e5f56f7fdc580347c938aaab56c25
statking label pearl
checking trader 0x82f80ff2d0ebf6680c98ad8fc874990b073f25cc
statking label pearl
checking trader 0x03429c1ab7d9d14baa42ded8a2dd7d684fc950ed
statking label pearl
checking trader 0x66a022b113b41e08d90cfd9468b8b6565d6ea995
statking label pearl
checking trader 0xfaa64c148c32af3552413438ec78599bffbd0

Labeling traders by staking: 100%|██████████| 204/204 [00:00<00:00, 415.07trader/s]


statking label pearl
checking trader 0x8cedb179299b99eeef4f6b231bc194952a339557
statking label pearl
checking trader 0x96d56cf7c906ab13752d5770e93e69330d050f5b
statking label pearl
checking trader 0xb972c2fdd528c3a56a6548c1247b9f68a00beae8
statking label pearl
checking trader 0xffc47cb1ecd41daae58e39fd4193d6fe9a6f5d2e
statking label pearl
checking trader 0x2ff064d951996c9fe70d6ba22d8684f37b2e24ec
trader address not found in the service map
statking label 
checking trader 0xdb741a8f175b9baadd9b6777c1d57322117266e3
statking label pearl
checking trader 0x8e9d20cab5a3ed63ed7984092dd214e012a919bb
statking label pearl
checking trader 0xac3ebb0ab2e0dc9aff761a9841e91e02e537cdbf
statking label pearl
checking trader 0x6ed28d3d8996dccc661559cd34a160b18cd3c7a8
statking label 
checking trader 0xc7fc9c1e1ba6bb6a49f62b7b0d8a77d6d3c9dfbc
statking label pearl
checking trader 0x6957f7ac4a0a09f237a901749e518a678d1a614a
statking label pearl
checking trader 0xe715cc8f264ab48f75bb1b5c11d7dbaf949d73c5
statki

In [6]:
trades_df.loc[trades_df["market_creator"]=="pearl"].staking.value_counts()

staking
         808
pearl    670
Name: count, dtype: int64

In [7]:
trades_df['staking'] = trades_df['staking'].replace({
    "": "non_staking",
    "pearl": "staking"
})

In [8]:
trades_df.loc[trades_df["market_creator"]=="pearl"].staking.value_counts()

staking
non_staking    808
staking        670
Name: count, dtype: int64

In [11]:
trades_df.market_creator.value_counts()

market_creator
quickstart    3394
pearl         1478
Name: count, dtype: int64

In [12]:
trades_all = trades_df.copy(deep=True)
trades_all["market_creator"] = "all"

In [13]:

# merging both dataframes
all_filtered_trades = pd.concat([trades_df, trades_all], ignore_index=True)
all_filtered_trades = all_filtered_trades.sort_values(
    by="creation_timestamp", ascending=True
)

In [14]:
all_filtered_trades.market_creator.value_counts()

market_creator
all           4872
quickstart    3394
pearl         1478
Name: count, dtype: int64

In [15]:
all_filtered_trades = all_filtered_trades.loc[
    all_filtered_trades["market_creator"] == "all"
]

In [16]:
all_filtered_trades.staking.value_counts()

staking
              2503
quickstart    1699
pearl          670
Name: count, dtype: int64